In [1]:
import pandas as pd

from urllib.request import Request, urlopen
from bs4 import BeautifulSoup
from urllib.error import URLError, HTTPError

In [3]:
import gspread
from gspread_dataframe import set_with_dataframe
from google.oauth2.service_account import Credentials
from pydrive.auth import GoogleAuth
from pydrive.drive import GoogleDrive

scopes = ['https://www.googleapis.com/auth/spreadsheets',
          'https://www.googleapis.com/auth/drive']

credentials = Credentials.from_service_account_file('gbq.json', scopes=scopes)

gc = gspread.authorize(credentials)

gauth = GoogleAuth()
drive = GoogleDrive(gauth)

# open a google sheet
gs = gc.open_by_key('1nVyKyf4dVwrCleXtGz3gH7b6Hvs08pLsDr_ENfwL4LM')# select a work sheet from its name
# worksheet1 = gs.worksheet('Sheet1')

In [4]:
url = "https://fbref.com/en/comps/24/Serie-A-Stats"

headers = {'User-Agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/99.0.4844.51 Safari/537.36'}

try:
    response = urlopen(url)
    html = response.read()
    print(html)
    
except HTTPError as e:
    print(e.status, e.reason)
    
except URLError as e:
    print(e.reason)

b'    \n      \n<!DOCTYPE html>\n<html data-version="klecko-" data-root="/home/fb/deploy/www/base" lang="en" class="no-js" >\n<head>\n    <meta charset="utf-8">\n    <meta http-equiv="x-ua-compatible" content="ie=edge">\n    <meta name="viewport" content="width=device-width, initial-scale=1.0, maximum-scale=2.0" />\n    <link rel="dns-prefetch" href="https://cdn.ssref.net/req/202306051" />\n<!-- Quantcast Choice. Consent Manager Tag v2.0 (for TCF 2.0) -->\n<script type="text/javascript" async=true>\n    (function() {\n\tvar host = window.location.hostname;\n\tvar element = document.createElement(\'script\');\n\tvar firstScript = document.getElementsByTagName(\'script\')[0];\n\tvar url = \'https://cmp.quantcast.com\'\n\t    .concat(\'/choice/\', \'XwNYEpNeFfhfr\', \'/\', host, \n\t\t    \'/choice.js?tag_version=V2\');\n\tvar uspTries = 0;\n\tvar uspTriesLimit = 3;\n\telement.async = true;\n\telement.type = \'text/javascript\';\n\telement.src = url;\n\t\n\tfirstScript.parentNode.insertBe

In [5]:
html = html.decode('utf-8')
type(html)

str

In [6]:
html

'    \n      \n<!DOCTYPE html>\n<html data-version="klecko-" data-root="/home/fb/deploy/www/base" lang="en" class="no-js" >\n<head>\n    <meta charset="utf-8">\n    <meta http-equiv="x-ua-compatible" content="ie=edge">\n    <meta name="viewport" content="width=device-width, initial-scale=1.0, maximum-scale=2.0" />\n    <link rel="dns-prefetch" href="https://cdn.ssref.net/req/202306051" />\n<!-- Quantcast Choice. Consent Manager Tag v2.0 (for TCF 2.0) -->\n<script type="text/javascript" async=true>\n    (function() {\n\tvar host = window.location.hostname;\n\tvar element = document.createElement(\'script\');\n\tvar firstScript = document.getElementsByTagName(\'script\')[0];\n\tvar url = \'https://cmp.quantcast.com\'\n\t    .concat(\'/choice/\', \'XwNYEpNeFfhfr\', \'/\', host, \n\t\t    \'/choice.js?tag_version=V2\');\n\tvar uspTries = 0;\n\tvar uspTriesLimit = 3;\n\telement.async = true;\n\telement.type = \'text/javascript\';\n\telement.src = url;\n\t\n\tfirstScript.parentNode.insertBef

In [7]:
def trata_html(input):
    return " ".join(html.split()).replace('> <','><')

html = trata_html(html)
html

'<!DOCTYPE html><html data-version="klecko-" data-root="/home/fb/deploy/www/base" lang="en" class="no-js" ><head><meta charset="utf-8"><meta http-equiv="x-ua-compatible" content="ie=edge"><meta name="viewport" content="width=device-width, initial-scale=1.0, maximum-scale=2.0" /><link rel="dns-prefetch" href="https://cdn.ssref.net/req/202306051" /><!-- Quantcast Choice. Consent Manager Tag v2.0 (for TCF 2.0) --><script type="text/javascript" async=true> (function() { var host = window.location.hostname; var element = document.createElement(\'script\'); var firstScript = document.getElementsByTagName(\'script\')[0]; var url = \'https://cmp.quantcast.com\' .concat(\'/choice/\', \'XwNYEpNeFfhfr\', \'/\', host, \'/choice.js?tag_version=V2\'); var uspTries = 0; var uspTriesLimit = 3; element.async = true; element.type = \'text/javascript\'; element.src = url; firstScript.parentNode.insertBefore(element, firstScript); function makeStub() { var TCF_LOCATOR_NAME = \'__tcfapiLocator\'; var queue

In [8]:
soup = BeautifulSoup(html, 'html.parser')

In [32]:
classificacao = soup.find('table', id="results2023241_overall").find_all('tbody')

lista_equipes = []
for equipe in classificacao[0].find_all('tr'):
    dict_equipe = {}
    dict_equipe[equipe.find('th').get('data-stat')] = equipe.find('th').getText()
    for info in equipe.find_all('td'):
        dict_equipe[info.get('data-stat')] = info.getText()
    
    lista_equipes.append(dict_equipe)

df_classificacao = pd.DataFrame(lista_equipes)

# df_classificacao['xg_against'] = df_classificacao['xg_against'].astype(float)
# df_classificacao['xg_diff'] = df_classificacao['xg_diff'].astype(float)
# df_classificacao['xg_diff_per90'] = df_classificacao['xg_diff_per90'].astype(float)

df_classificacao

rank              team games wins ties losses goals_for goals_against  \
0     1     Botafogo (RJ)     9    7    0      2        16             7   
1     2         Palmeiras     9    5    4      0        20             8   
2     3  Atlético Mineiro     9    5    2      2        13             7   
3     4            Grêmio     9    5    2      2        14            12   
4     5          Flamengo     9    5    1      3        18            11   
5     6        Fluminense     9    5    1      3        14             9   
6     7    Atl Paranaense     9    5    0      4        12            11   
7     8         São Paulo     9    4    3      2        15             9   
8     9         Fortaleza     9    3    5      1        12             6   
9    10          Cruzeiro     9    4    1      4        12             8   
10   11        Bragantino     9    3    4      2        14            13   
11   12            Santos     9    3    3      3         9             8   
12   13     Internacional     9    3    2      4         8            12   
13   14            Cuiabá     9    3    2      4         8            13   
14   15             Bahia     9    2    2      5         9            14   
15   16       Corinthians     9    2    2      5         8            14   
16   17             Goiás     9    2    1      6         7            16   
17   18      América (MG)     9    2    1      6         9            20   
18   19     Vasco da Gama     9    1    3      5         9            17   
19   20          Coritiba     9    0    3      6         8            20   

   goal_diff points points_avg xg_for xg_against xg_diff xg_diff_per90 last_5  \
0         +9     21       2.33   13.4       10.9    +2.4         +0.27  WLWWL   
1        +12     19       2.11   15.9        6.4    +9.5         +1.06  WDDDW   
2         +6     17       1.89   12.7        9.3    +3.4         +0.37  WWWDW   
3         +2     17       1.89   10.7       14.0    -3.3         -0.37  LDWWW   
4         +7     16       1.78   16.0       10.0    +6.0         +0.66  WWWDW   
5         +5     16       1.78   12.5       14.4    -1.9         -0.21  WWLLW   
6         +1     15       1.67   10.5        9.5    +1.0         +0.11  WWLLW   
7         +6     15       1.67   13.1       10.0    +3.1         +0.35  DDWWL   
8         +6     14       1.56   15.7        6.9    +8.8         +0.97  DDLWD   
9         +4     13       1.44   14.6       11.5    +3.1         +0.35  LWLDL   
10        +1     13       1.44   12.4       11.4    +1.0         +0.11  DDWWL   
11        +1     12       1.33    9.8       11.7    -1.9         -0.22  WWDLD   
12        -4     11       1.22    8.7       13.0    -4.3         -0.48  LLLWD   
13        -5     11       1.22    8.1       12.6    -4.6         -0.51  LLWDW   
14        -5      8       0.89   10.2       10.5    -0.3         -0.04  LLDLD   
15        -6      8       0.89    8.7       10.4    -1.7         -0.19  LDLWL   
16        -9      7       0.78    8.0       13.3    -5.3         -0.59  LWDLL   
17       -11      7       0.78   10.5       16.5    -5.9         -0.66  DLWLW   
18        -8      6       0.67   10.1       11.8    -1.6         -0.18  DLLLL   
19       -12      3       0.33    7.2       14.6    -7.4         -0.82  DLLDL   

   attendance_per_g                      top_team_scorers  \
0             4,742                   Tiquinho Soares - 6   
1             7,167              Raphael Veiga, Artur - 4   
2            22,329                              Hulk - 5   
3            11,367  Luis Suárez, Franco Cristaldo... - 2   
4            19,197   Léo Pereira, Gabriel Barbosa... - 3   
5             9,650                             Ganso - 3   
6            10,111                       Vitor Roque - 3   
7            21,775                  Jonathan Calleri - 4   
8             7,668                            Moises - 3   
9             4,321                          Gilberto - 3   
10            1,198              

In [33]:
pag_classificacao = gs.worksheet('Classificação')

pag_classificacao.clear()
set_with_dataframe(worksheet=pag_classificacao, dataframe=df_classificacao, include_index=False,
include_column_header=True, resize=True)

In [26]:
stats_time = soup.find('table', id="stats_squads_standard_for").find_all('tbody')

lista_equipes = []
for equipe in stats_time[0].find_all('tr'):
    dict_equipe = {}
    dict_equipe[equipe.find('th').get('data-stat')] = equipe.find('th').getText()
    for info in equipe.find_all('td'):
        dict_equipe[info.get('data-stat')] = info.getText()
    
    lista_equipes.append(dict_equipe)

df_stats_time = pd.DataFrame(lista_equipes)
df_stats_time

team players_used avg_age possession games games_starts  \
0       América (MG)           32    30.5       42.6     9           99   
1     Atl Paranaense           26    26.3       48.3     9           99   
2   Atlético Mineiro           25    29.4       58.0     9           99   
3              Bahia           24    26.4       51.1     9           99   
4      Botafogo (RJ)           28    29.0       43.0     9           99   
5         Bragantino           25    24.5       55.1     9           99   
6        Corinthians           29    27.3       44.4     9           99   
7           Coritiba           28    27.8       44.0     9           99   
8           Cruzeiro           23    28.7       54.0     9           99   
9             Cuiabá           23    28.7       44.0     9           99   
10          Flamengo           24    26.9       60.2     9           99   
11        Fluminense           25    29.5       62.6     9           99   
12         Fortaleza           24    29.7       48.3     9           99   
13             Goiás           28    28.5       46.9     9           99   
14            Grêmio           28    28.3       43.2     9           99   
15     Internacional           26    28.3       50.4     9           99   
16         Palmeiras           26    27.6       55.6     9           99   
17            Santos           30    26.2       43.2     9           99   
18         São Paulo           24    27.3       58.9     9           99   
19     Vasco da Gama           26    25.3       46.1     9           99   

   minutes minutes_90s goals assists  ... goals_per90 assists_per90  \
0      810         9.0     9       6  ...        1.00          0.67   
1      810         9.0    12      11  ...        1.33          1.22   
2      810         9.0    13       8  ...        1.44          0.89   
3      810         9.0     8       5  ...        0.89          0.56   
4      810         9.0    16      11  ...        1.78          1.22   
5      810         9.0    14      11  ...        1.56          1.22   
6      810         9.0     7       4  ...        0.78          0.44   
7      810         9.0     8       5  ...        0.89          0.56   
8      810         9.0    12      10  ...        1.33          1.11   
9      810         9.0     7       5  ...        0.78          0.56   
10     810         9.0    18      13  ...        2.00          1.44   
11     810         9.0    14      10  ...        1.56          1.11   
12     810         9.0    12       7  ...        1.33          0.78   
13     810         9.0     7       5  ...        0.78          0.56   
14     810         9.0    14       8  ...        1.56          0.89   
15     810         9.0     8       6  ...        0.89          0.67   
16     810         9.0    19      15  ...        2.11          1.67   
17     810         9.0     9       6  ...        1.00          0.67   
18     810         9.0    15      12  ...        1.67          1.33   
19     810         9.0     9       6  ...        1.00          0.67   

   goals_assists_per90 goals_pens_per90 goals_assists_pens_per90 xg_per90  \
0                 1.67             0.67                     1.33     1.17   
1                 2.56             1.33                     2.56     1.17   
2                 2.33             1.22                     2.11     1.41   
3                 1.44             0.89                     1.44     1.13   
4                 3.00             1.44                     2.67     1.48   
5                 2.78             1.56                     2.78     1.38   
6                 1.22             0.67                     1.11     0.97   
7                 1.44             0.78                     1.33     0.80   
8                 2.44             1.33                     2.44     1.62   
9                 1.33             0.78                     1.33     0.90   
10                3.44             1.56                     3.00     1.78   
11                2.67  

In [27]:
pag_stats_time = gs.worksheet('Estats Time')

pag_stats_time.clear()
set_with_dataframe(worksheet=pag_stats_time, dataframe=df_stats_time, include_index=False,
include_column_header=True, resize=True)

In [28]:
stats_goleiros = soup.find('table', id="stats_squads_keeper_for").find_all('tbody')

lista_equipes = []
for equipe in stats_goleiros[0].find_all('tr'):
    dict_equipe = {}
    dict_equipe[equipe.find('th').get('data-stat')] = equipe.find('th').getText()
    for info in equipe.find_all('td'):
        dict_equipe[info.get('data-stat')] = info.getText()
    
    lista_equipes.append(dict_equipe)

df_stats_goleiros = pd.DataFrame(lista_equipes)
df_stats_goleiros

team players_used gk_games gk_games_starts gk_minutes  \
0       América (MG)            2        9               9        808   
1     Atl Paranaense            1        9               9        810   
2   Atlético Mineiro            1        9               9        810   
3              Bahia            1        9               9        810   
4      Botafogo (RJ)            1        9               9        810   
5         Bragantino            2        9               9        810   
6        Corinthians            1        9               9        810   
7           Coritiba            2        9               9        810   
8           Cruzeiro            1        9               9        810   
9             Cuiabá            1        9               9        810   
10          Flamengo            2        9               9        810   
11        Fluminense            1        9               9        810   
12         Fortaleza            3        9               9        810   
13             Goiás            2        9               9        810   
14            Grêmio            2        9               9        810   
15     Internacional            2        9               9        810   
16         Palmeiras            1        9               9        810   
17            Santos            1        9               9        810   
18         São Paulo            1        9               9        810   
19     Vasco da Gama            1        9               9        810   

   minutes_90s gk_goals_against gk_goals_against_per90  \
0          9.0               20                   2.23   
1          9.0               11                   1.22   
2          9.0                7                   0.78   
3          9.0               14                   1.56   
4          9.0                7                   0.78   
5          9.0               13                   1.44   
6          9.0               14                   1.56   
7          9.0               20                   2.22   
8          9.0                8                   0.89   
9          9.0               13                   1.44   
10         9.0               11                   1.22   
11         9.0                9                   1.00   
12         9.0                6                   0.67   
13         9.0               16                   1.78   
14         9.0               12                   1.33   
15         9.0               12                   1.33   
16         9.0                8                   0.89   
17         9.0                8                   0.89   
18         9.0                9                   1.00   
19         9.0               17                   1.89   

   gk_shots_on_target_against gk_saves  ... gk_wins gk_ties gk_losses  \
0                          55       35  ...       2       1         6   
1                          35       24  ...       5       0         4   
2                          31       24  ...       5       2         2   
3                          42       28  ...       2       2         5   
4                          43       36  ...       7       0         2   
5                          32       19  ...       3       4         2   
6                          40       26  ...       2       2         5   
7                          55       36  ...       0       3         6   
8                          38       30  ...       4       1         4   
9                          39       26  ...       3       2         4   
10                         43       32  ...       5       1         3   
11                         42       33  ...       5       1         3   
12                         37       31  ...       3       5         1   
13                         45       30  ...       2       1         6   
14                         47       35  ...       5       2         2   
15                         38       25  ...       3       2         4   
16                    

In [29]:
pag_goleiros = gs.worksheet('Goleiros')

pag_goleiros.clear()
set_with_dataframe(worksheet=pag_goleiros, dataframe=df_stats_goleiros, include_index=False,
include_column_header=True, resize=True)

In [30]:
stats_goleiros_adv = soup.find('table', id="stats_squads_keeper_adv_for").find_all('tbody')

lista_equipes = []
for equipe in stats_goleiros_adv[0].find_all('tr'):
    dict_equipe = {}
    dict_equipe[equipe.find('th').get('data-stat')] = equipe.find('th').getText()
    for info in equipe.find_all('td'):
        dict_equipe[info.get('data-stat')] = info.getText()
    
    lista_equipes.append(dict_equipe)

df_stats_goleiros_adv = pd.DataFrame(lista_equipes)
df_stats_goleiros_adv

team players_used minutes_90s gk_goals_against  \
0       América (MG)            2         9.0               20   
1     Atl Paranaense            1         9.0               11   
2   Atlético Mineiro            1         9.0                7   
3              Bahia            1         9.0               14   
4      Botafogo (RJ)            1         9.0                7   
5         Bragantino            2         9.0               13   
6        Corinthians            1         9.0               14   
7           Coritiba            2         9.0               20   
8           Cruzeiro            1         9.0                8   
9             Cuiabá            1         9.0               13   
10          Flamengo            2         9.0               11   
11        Fluminense            1         9.0                9   
12         Fortaleza            3         9.0                6   
13             Goiás            2         9.0               16   
14            Grêmio            2         9.0               12   
15     Internacional            2         9.0               12   
16         Palmeiras            1         9.0                8   
17            Santos            1         9.0                8   
18         São Paulo            1         9.0                9   
19     Vasco da Gama            1         9.0               17   

   gk_pens_allowed gk_free_kick_goals_against gk_corner_kick_goals_against  \
0                1                          2                            0   
1                1                          0                            2   
2                1                          0                            0   
3                1                          1                            0   
4                0                          0                            1   
5                3                          0                            2   
6                2                          0                            4   
7                2                          1                            1   
8                0                          1                            1   
9                1                          0                            2   
10               2                          0                            1   
11               0                          0                            1   
12               0                          0                            1   
13               2                          0                            5   
14               1                          0                            4   
15               0                          1                            1   
16               0                          0                            0   
17               0                          0                            3   
18               2                          0                            0   
19               0                          0                            1   

   gk_own_goals_against gk_psxg gk_psnpxg_per_shot_on_target_against  ...  \
0                     1    19.1                                 0.31  ...   
1                     0     9.3                                 0.24  ...   
2                     0     9.8                                 0.29  ...   
3                     0    13.2                                 0.32  ...   
4                     0     8.7                                 0.21  ...   
5                     0    12.6                                 0.30  ...   
6                     0    13.6                                 0.29  ...   
7                     1    16.0                                 0.26  ...   
8                     0    10.2                                 0.28  ...   
9                     0    13.4                                 0.32  ...   
10                    0    10.4                                 0.21  ...   
11                    0    13.4                                 0.

In [31]:
pag_goleiros_adv = gs.worksheet('Goleiros adv')

pag_goleiros_adv.clear()
set_with_dataframe(worksheet=pag_goleiros_adv, dataframe=df_stats_goleiros_adv, include_index=False,
include_column_header=True, resize=True)

In [34]:
stats_finalizacoes = soup.find('table', id="stats_squads_shooting_for").find_all('tbody')

lista_equipes = []
for equipe in stats_finalizacoes[0].find_all('tr'):
    dict_equipe = {}
    dict_equipe[equipe.find('th').get('data-stat')] = equipe.find('th').getText()
    for info in equipe.find_all('td'):
        dict_equipe[info.get('data-stat')] = info.getText()
    
    lista_equipes.append(dict_equipe)

df_stats_finalizacoes = pd.DataFrame(lista_equipes)
df_stats_finalizacoes

team players_used minutes_90s goals shots shots_on_target  \
0       América (MG)           32         9.0     9   124              34   
1     Atl Paranaense           26         9.0    12   125              38   
2   Atlético Mineiro           25         9.0    13   123              47   
3              Bahia           24         9.0     8   125              38   
4      Botafogo (RJ)           28         9.0    16   132              41   
5         Bragantino           25         9.0    14   128              49   
6        Corinthians           29         9.0     7   105              34   
7           Coritiba           28         9.0     8    95              36   
8           Cruzeiro           23         9.0    12   151              48   
9             Cuiabá           23         9.0     7   110              32   
10          Flamengo           24         9.0    18   136              43   
11        Fluminense           25         9.0    14   118              42   
12         Fortaleza           24         9.0    12   148              53   
13             Goiás           28         9.0     7   117              36   
14            Grêmio           28         9.0    14   113              45   
15     Internacional           26         9.0     8   117              37   
16         Palmeiras           26         9.0    19   161              51   
17            Santos           30         9.0     9   106              34   
18         São Paulo           24         9.0    15   128              42   
19     Vasco da Gama           26         9.0     9   111              33   

   shots_on_target_pct shots_per90 shots_on_target_per90 goals_per_shot  \
0                 27.4       13.78                  3.78           0.05   
1                 30.4       13.89                  4.22           0.10   
2                 38.2       13.67                  5.22           0.09   
3                 30.4       13.89                  4.22           0.06   
4                 31.1       14.67                  4.56           0.10   
5                 38.3       14.22                  5.44           0.11   
6                 32.4       11.67                  3.78           0.06   
7                 37.9       10.56                  4.00           0.07   
8                 31.8       16.78                  5.33           0.08   
9                 29.1       12.22                  3.56           0.06   
10                31.6       15.11                  4.78           0.10   
11                35.6       13.11                  4.67           0.12   
12                35.8       16.44                  5.89           0.08   
13                30.8       13.00                  4.00           0.06   
14                39.8       12.56                  5.00           0.11   
15                31.6       13.00                  4.11           0.07   
16                31.7       17.89                  5.67           0.11   
17                32.1       11.78                  3.78           0.08   
18                32.8       14.22                  4.67           0.12   
19                29.7       12.33                  3.67           0.07   

   goals_per_shot_on_target average_shot_distance shots_free_kicks pens_made  \
0                      0.18                  20.7                5         3   
1                      0.32                  19.9                8         0   
2                      0.23                  19.7               12         2   
3                      0.21                  19.0                7         0   
4                      0.32                  19.1                3         3   
5                      0.29                  19.6                4         0   
6                      0.18                  20.7                5         1   
7                      0.19                  22.2                8         1   
8                      0.25                  18.4                6         0   
9                     

In [35]:
pag_finalizacoes = gs.worksheet('Finalizações')

pag_finalizacoes.clear()
set_with_dataframe(worksheet=pag_finalizacoes, dataframe=df_stats_finalizacoes, include_index=False,
include_column_header=True, resize=True)

In [36]:
stats_passes = soup.find('table', id="stats_squads_passing_for").find_all('tbody')

lista_equipes = []
for equipe in stats_passes[0].find_all('tr'):
    dict_equipe = {}
    dict_equipe[equipe.find('th').get('data-stat')] = equipe.find('th').getText()
    for info in equipe.find_all('td'):
        dict_equipe[info.get('data-stat')] = info.getText()
    
    lista_equipes.append(dict_equipe)

df_stats_passes = pd.DataFrame(lista_equipes)
df_stats_passes

team players_used minutes_90s passes_completed passes  \
0       América (MG)           32         9.0             2542   3496   
1     Atl Paranaense           26         9.0             3267   4176   
2   Atlético Mineiro           25         9.0             4104   4993   
3              Bahia           24         9.0             3422   4337   
4      Botafogo (RJ)           28         9.0             2981   3760   
5         Bragantino           25         9.0             3327   4367   
6        Corinthians           29         9.0             3439   4271   
7           Coritiba           28         9.0             2934   3795   
8           Cruzeiro           23         9.0             3764   4705   
9             Cuiabá           23         9.0             2962   3875   
10          Flamengo           24         9.0             4668   5448   
11        Fluminense           25         9.0             4739   5514   
12         Fortaleza           24         9.0             3331   4206   
13             Goiás           28         9.0             3116   3946   
14            Grêmio           28         9.0             2848   3826   
15     Internacional           26         9.0             3508   4356   
16         Palmeiras           26         9.0             3875   4751   
17            Santos           30         9.0             2709   3643   
18         São Paulo           24         9.0             4418   5238   
19     Vasco da Gama           26         9.0             2850   3778   

   passes_pct passes_total_distance passes_progressive_distance  \
0        72.7                 46958                       20351   
1        78.2                 62155                       22015   
2        82.2                 73297                       23992   
3        78.9                 60719                       21745   
4        79.3                 53014                       20477   
5        76.2                 56936                       22038   
6        80.5                 59254                       21030   
7        77.3                 54089                       21231   
8        80.0                 70962                       25552   
9        76.4                 54117                       22645   
10       85.7                 80793                       25947   
11       85.9                 70931                       23345   
12       79.2                 59404                       20745   
13       79.0                 58341                       21710   
14       74.4                 46097                       19463   
15       80.5                 58835                       20577   
16       81.6                 75999                       26149   
17       74.4                 46113                       18118   
18       84.3                 77052                       25248   
19       75.4                 53412                       19718   

   passes_completed_short passes_short  ... passes_pct_long assists xg_assist  \
0                    1100         1317  ...            50.3       6       6.8   
1                    1305         1494  ...            54.6      11       8.6   
2                    1748         1946  ...            55.8       8       8.8   
3                    1508         1726  ...            55.6       5       6.0   
4                    1345         1520  ...            54.6      11       7.9   
5                    1621         1852  ...            47.7      11       9.3   
6                    1637         1811  ...            52.8       4       5.5   
7                    1273         1480  ...            53.3       5       5.0   
8                    1573         1799  ...            61.8      10      10.8   
9                    1346         1573  ...            56.7       5       6.7   
10                   2197         2404  ...            66.6      13      10.5   
11                   2699         2911  ...            58.3      10       9.6   
12                   

In [38]:
pag_passes = gs.worksheet('Passes')

pag_passes.clear()
set_with_dataframe(worksheet=pag_passes, dataframe=df_stats_passes, include_index=False,
include_column_header=True, resize=True)

In [39]:
stats_passes_tipo = soup.find('table', id="stats_squads_passing_types_for").find_all('tbody')

lista_equipes = []
for equipe in stats_passes_tipo[0].find_all('tr'):
    dict_equipe = {}
    dict_equipe[equipe.find('th').get('data-stat')] = equipe.find('th').getText()
    for info in equipe.find_all('td'):
        dict_equipe[info.get('data-stat')] = info.getText()
    
    lista_equipes.append(dict_equipe)

df_stats_passes_tipo = pd.DataFrame(lista_equipes)
df_stats_passes_tipo 

team players_used minutes_90s passes passes_live passes_dead  \
0       América (MG)           32         9.0   3496        3050         424   
1     Atl Paranaense           26         9.0   4176        3695         464   
2   Atlético Mineiro           25         9.0   4993        4556         422   
3              Bahia           24         9.0   4337        3832         496   
4      Botafogo (RJ)           28         9.0   3760        3331         415   
5         Bragantino           25         9.0   4367        3830         519   
6        Corinthians           29         9.0   4271        3814         444   
7           Coritiba           28         9.0   3795        3299         481   
8           Cruzeiro           23         9.0   4705        4170         512   
9             Cuiabá           23         9.0   3875        3373         486   
10          Flamengo           24         9.0   5448        5008         422   
11        Fluminense           25         9.0   5514        5021         476   
12         Fortaleza           24         9.0   4206        3773         416   
13             Goiás           28         9.0   3946        3403         521   
14            Grêmio           28         9.0   3826        3330         480   
15     Internacional           26         9.0   4356        3885         455   
16         Palmeiras           26         9.0   4751        4261         472   
17            Santos           30         9.0   3643        3171         454   
18         São Paulo           24         9.0   5238        4777         446   
19     Vasco da Gama           26         9.0   3778        3282         479   

   passes_free_kicks through_balls passes_switches crosses throw_ins  \
0                125             7              32     174       164   
1                128            13              56     156       198   
2                116            19              36     163       177   
3                172             8              34     174       183   
4                127             6              28     148       166   
5                128             5              33     183       237   
6                130            11              28     141       170   
7                138            11              35     131       199   
8                148             6              52     224       203   
9                168             5              31     189       178   
10               132            11              54     154       158   
11               160             7              25     161       167   
12               127            12              28     194       161   
13               171             5              37     196       190   
14               150             5              13     122       157   
15               134            12              22     169       178   
16               141             7              44     217       184   
17               125             9              20     143       201   
18               135            11              49     164       170   
19               130             4              18     217       200   

   corner_kicks corner_kicks_in corner_kicks_out corner_kicks_straight  \
0            40               8               16                     3   
1            44              15               26                     0   
2            48              21               24                     0   
3            51              23               11                     1   
4            44              15               28                     0   
5            49              31                7                     0   
6            50              11               36                     0   
7            41              21               12                     0   
8            69              32               14                     1   
9            39              15               22                     0   
10      

In [40]:
pag_passes_tipo = gs.worksheet('Passes Tipo')

pag_passes_tipo.clear()
set_with_dataframe(worksheet=pag_passes_tipo, dataframe=df_stats_passes_tipo, include_index=False,
include_column_header=True, resize=True)

In [41]:
gols_chances_criadas = soup.find('table', id="stats_squads_gca_for").find_all('tbody')

lista_equipes = []
for equipe in gols_chances_criadas[0].find_all('tr'):
    dict_equipe = {}
    dict_equipe[equipe.find('th').get('data-stat')] = equipe.find('th').getText()
    for info in equipe.find_all('td'):
        dict_equipe[info.get('data-stat')] = info.getText()
    
    lista_equipes.append(dict_equipe)

df_gols_chances_criadas = pd.DataFrame(lista_equipes)
df_gols_chances_criadas

team players_used minutes_90s  sca sca_per90 sca_passes_live  \
0       América (MG)           32         9.0  215     23.89             164   
1     Atl Paranaense           26         9.0  213     23.67             147   
2   Atlético Mineiro           25         9.0  218     24.22             147   
3              Bahia           24         9.0  224     24.89             160   
4      Botafogo (RJ)           28         9.0  235     26.11             160   
5         Bragantino           25         9.0  220     24.44             176   
6        Corinthians           29         9.0  172     19.11             126   
7           Coritiba           28         9.0  164     18.22             112   
8           Cruzeiro           23         9.0  268     29.78             194   
9             Cuiabá           23         9.0  193     21.44             129   
10          Flamengo           24         9.0  255     28.33             196   
11        Fluminense           25         9.0  216     24.00             170   
12         Fortaleza           24         9.0  253     28.11             182   
13             Goiás           28         9.0  202     22.44             126   
14            Grêmio           28         9.0  202     22.44             134   
15     Internacional           26         9.0  210     23.33             159   
16         Palmeiras           26         9.0  292     32.44             212   
17            Santos           30         9.0  186     20.67             120   
18         São Paulo           24         9.0  222     24.67             164   
19     Vasco da Gama           26         9.0  195     21.67             133   

   sca_passes_dead sca_take_ons sca_shots sca_fouled sca_defense gca  \
0               11           18         8         12           2  15   
1               18           17        12         11           8  21   
2               16           17        18         18           2  23   
3               19           17        14         11           3  16   
4               21           20        22         10           2  28   
5                6           16        13          8           1  24   
6               12           14        11          6           3  13   
7               17           14         6         12           3  14   
8               25           22        14         11           2  23   
9               22           15        10         15           2  11   
10              14           19        15          8           3  32   
11               9           13        13          7           4  25   
12              15           17        20         15           4  19   
13              27           19        13         12           5  12   
14              28           14        13         11           2  23   
15              13           12        15          9           2  15   
16              26           18        18         10           8  31   
17              23           12        10         16           5  16   
18              16           20        14          4           4  24   
19              15           18         8         18           3  14   

   gca_per90 gca_passes_live gca_passes_dead gca_take_ons gca_shots  \
0       1.67              11               0            1         1   
1       2.33              19               1            1         0   
2       2.56              17               0            2         0   
3       1.78               7               2            3         2   
4       3.11              15               2            3         5   
5       2.67              18               0            3         2   
6       1.44              11               0            0         1   
7       1.56               9               3            1         1   
8       2.56              21               1            1         0   
9       1.22               8               0            1         2   
10      3.56              18             

In [42]:
pag_chances_criadas = gs.worksheet('Chances Criadas')

pag_chances_criadas.clear()
set_with_dataframe(worksheet=pag_chances_criadas, dataframe=df_gols_chances_criadas, include_index=False,
include_column_header=True, resize=True)

In [43]:
stats_defesa = soup.find('table', id="stats_squads_defense_for").find_all('tbody')

lista_equipes = []
for equipe in stats_defesa[0].find_all('tr'):
    dict_equipe = {}
    dict_equipe[equipe.find('th').get('data-stat')] = equipe.find('th').getText()
    for info in equipe.find_all('td'):
        dict_equipe[info.get('data-stat')] = info.getText()
    
    lista_equipes.append(dict_equipe)

df_stats_defesa = pd.DataFrame(lista_equipes)
df_stats_defesa

team players_used minutes_90s tackles tackles_won  \
0       América (MG)           32         9.0     129          79   
1     Atl Paranaense           26         9.0     139          87   
2   Atlético Mineiro           25         9.0     186         120   
3              Bahia           24         9.0     148          98   
4      Botafogo (RJ)           28         9.0     146          85   
5         Bragantino           25         9.0     151          90   
6        Corinthians           29         9.0     142          95   
7           Coritiba           28         9.0     178         103   
8           Cruzeiro           23         9.0     169          99   
9             Cuiabá           23         9.0     158          98   
10          Flamengo           24         9.0     139          95   
11        Fluminense           25         9.0     131          82   
12         Fortaleza           24         9.0     179         116   
13             Goiás           28         9.0     145          90   
14            Grêmio           28         9.0     148          95   
15     Internacional           26         9.0     148          93   
16         Palmeiras           26         9.0     135          82   
17            Santos           30         9.0     200         116   
18         São Paulo           24         9.0     145          97   
19     Vasco da Gama           26         9.0     164          95   

   tackles_def_3rd tackles_mid_3rd tackles_att_3rd challenge_tackles  \
0               56              54              19                47   
1               63              63              13                57   
2               83              76              27                92   
3               64              65              19                82   
4               66              69              11                87   
5               61              70              20                65   
6               88              41              13                73   
7               84              75              19                91   
8               82              70              17                72   
9               90              49              19                90   
10              47              65              27                64   
11              57              51              23                70   
12              91              70              18               102   
13              79              51              15                77   
14              76              55              17                68   
15              74              54              20                84   
16              65              55              15                60   
17              92              82              26                99   
18              61              67              17                79   
19              83              64              17                65   

   challenges challenge_tackles_pct challenges_lost blocks blocked_shots  \
0         167                  28.1             120    109            31   
1         151                  37.7              94    106            29   
2         211                  43.6             119    102            31   
3         191                  42.9             109     95            25   
4         188                  46.3             101     94            21   
5         173                  37.6             108    113            31   
6         169                  43.2              96    125            43   
7         215                  42.3             124    103            38   
8         163                  44.2              91     95            21   
9         221                  40.7             131     99            15   
10        181                  35.4             117     85            30   
11        150                  46.7              80    107            41   
12        215                  47.4             113    103       

In [46]:
pag_defesa = gs.worksheet('Defesa')

pag_defesa.clear()
set_with_dataframe(worksheet=pag_defesa, dataframe=df_stats_defesa, include_index=False,
include_column_header=True, resize=True)

In [45]:
stats_posse = soup.find('table', id="stats_squads_possession_for").find_all('tbody')

lista_equipes = []
for equipe in stats_posse[0].find_all('tr'):
    dict_equipe = {}
    dict_equipe[equipe.find('th').get('data-stat')] = equipe.find('th').getText()
    for info in equipe.find_all('td'):
        dict_equipe[info.get('data-stat')] = info.getText()
    
    lista_equipes.append(dict_equipe)

df_stats_posse = pd.DataFrame(lista_equipes)
df_stats_posse

team players_used possession minutes_90s touches  \
0       América (MG)           32       42.6         9.0    4529   
1     Atl Paranaense           26       48.3         9.0    5200   
2   Atlético Mineiro           25       58.0         9.0    6018   
3              Bahia           24       51.1         9.0    5347   
4      Botafogo (RJ)           28       43.0         9.0    4809   
5         Bragantino           25       55.1         9.0    5462   
6        Corinthians           29       44.4         9.0    5183   
7           Coritiba           28       44.0         9.0    4878   
8           Cruzeiro           23       54.0         9.0    5741   
9             Cuiabá           23       44.0         9.0    4859   
10          Flamengo           24       60.2         9.0    6429   
11        Fluminense           25       62.6         9.0    6489   
12         Fortaleza           24       48.3         9.0    5196   
13             Goiás           28       46.9         9.0    4977   
14            Grêmio           28       43.2         9.0    4941   
15     Internacional           26       50.4         9.0    5399   
16         Palmeiras           26       55.6         9.0    5729   
17            Santos           30       43.2         9.0    4779   
18         São Paulo           24       58.9         9.0    6238   
19     Vasco da Gama           26       46.1         9.0    4786   

   touches_def_pen_area touches_def_3rd touches_mid_3rd touches_att_3rd  \
0                   513            1429            1926            1241   
1                   499            1573            2537            1138   
2                   572            1715            3041            1320   
3                   532            1667            2521            1212   
4                   474            1446            2309            1110   
5                   493            1432            2401            1691   
6                   534            1796            2402            1041   
7                   587            1727            2206            1005   
8                   514            1652            2599            1562   
9                   449            1414            2287            1223   
10                  494            1552            3035            1901   
11                  719            2144            2766            1633   
12                  414            1324            2674            1272   
13                  657            1706            2191            1135   
14                  571            1476            2304            1208   
15                  472            1544            2709            1212   
16                  506            1618            2684            1482   
17                  520            1636            2165            1056   
18                  620            1815            3170            1303   
19                  548            1558            2218            1082   

   touches_att_pen_area  ... carries carries_distance  \
0                   180  ...    2483            15211   
1                   178  ...    2771            14383   
2                   168  ...    3562            19204   
3                   169  ...    2962            16875   
4                   176  ...    2716            16089   
5                   203  ...    3073            17036   
6                   133  ...    2859            14638   
7                   100  ...    2488            13737   
8                   197  ...    3176            17047   
9                   156  ...    2590            15296   
10                  243  ...    4085            21081   
11                  192  ...    4303            21170   
12                  224  ...    2993            17689   
13                  128  ...    2719            14994   
14                  159  ...    2462            11666   
15                  173  ...    3232            17302   
16                  214  ...    3480      

In [47]:
pag_posse = gs.worksheet('Posse de Bola')

pag_posse.clear()
set_with_dataframe(worksheet=pag_posse, dataframe=df_stats_posse, include_index=False,
include_column_header=True, resize=True)

In [48]:
stats_tempo_jogo = soup.find('table', id="stats_squads_playing_time_for").find_all('tbody')

lista_equipes = []
for equipe in stats_tempo_jogo[0].find_all('tr'):
    dict_equipe = {}
    dict_equipe[equipe.find('th').get('data-stat')] = equipe.find('th').getText()
    for info in equipe.find_all('td'):
        dict_equipe[info.get('data-stat')] = info.getText()
    
    lista_equipes.append(dict_equipe)

df_stats_tempo_jogo = pd.DataFrame(lista_equipes)
df_stats_tempo_jogo

team players_used avg_age games minutes minutes_per_game  \
0       América (MG)           32    30.5     9     810               90   
1     Atl Paranaense           26    26.3     9     810               90   
2   Atlético Mineiro           25    29.4     9     810               90   
3              Bahia           24    26.4     9     810               90   
4      Botafogo (RJ)           28    29.0     9     810               90   
5         Bragantino           25    24.5     9     810               90   
6        Corinthians           29    27.3     9     810               90   
7           Coritiba           28    27.8     9     810               90   
8           Cruzeiro           23    28.7     9     810               90   
9             Cuiabá           23    28.7     9     810               90   
10          Flamengo           24    26.9     9     810               90   
11        Fluminense           25    29.5     9     810               90   
12         Fortaleza           24    29.7     9     810               90   
13             Goiás           28    28.5     9     810               90   
14            Grêmio           28    28.3     9     810               90   
15     Internacional           26    28.3     9     810               90   
16         Palmeiras           26    27.6     9     810               90   
17            Santos           30    26.2     9     810               90   
18         São Paulo           24    27.3     9     810               90   
19     Vasco da Gama           26    25.3     9     810               90   

   minutes_pct minutes_90s games_starts minutes_per_start  ... unused_subs  \
0          100         9.0           99                81  ...          62   
1          100         9.0           99                79  ...          61   
2          100         9.0           99                81  ...          59   
3          100         9.0           99                81  ...          66   
4          100         9.0           99                81  ...          67   
5          100         9.0           99                76  ...          63   
6          100         9.0           99                82  ...          68   
7          100         9.0           99                80  ...          61   
8          100         9.0           99                81  ...          65   
9          100         9.0           99                80  ...          58   
10         100         9.0           99                80  ...          69   
11         100         9.0           99                81  ...          67   
12         100         9.0           99                81  ...          63   
13         100         9.0           99                81  ...          69   
14         100         9.0           99                81  ...          64   
15         100         9.0           99                79  ...          62   
16         100         9.0           99                82  ...          62   
17         100         9.0           99                80  ...          65   
18         100         9.0           99                81  ...          63   
19         100         9.0           99                81  ...          63   

   points_per_game on_goals_for on_goals_against plus_minus plus_minus_per90  \
0             0.78            9               20        -11            -1.22   
1             1.67           12               11         +1            +0.11   
2             1.89           13                7         +6            +0.67   
3             0.89            9               14         -5            -0.56   
4             2.33           16                7         +9            +1.00   
5             1.44           14               13         +1            +0.11   
6             0.89            8               14         -6            -0.67   
7             0.33            8               20        -12            -1.33   
8             1.44           12                8         +4 

In [49]:
pag_tempo = gs.worksheet('Tempo de Jogo')

pag_tempo.clear()
set_with_dataframe(worksheet=pag_tempo, dataframe=df_stats_tempo_jogo, include_index=False,
include_column_header=True, resize=True)

In [21]:
stats_diversas = soup.find('table', id="stats_squads_misc_for").find_all('tbody')

lista_equipes = []
for equipe in stats_diversas[0].find_all('tr'):
    dict_equipe = {}
    dict_equipe[equipe.find('th').get('data-stat')] = equipe.find('th').getText()
    for info in equipe.find_all('td'):
        dict_equipe[info.get('data-stat')] = info.getText()
    
    lista_equipes.append(dict_equipe)

df_stats_diversas = pd.DataFrame(lista_equipes)
df_stats_diversas

team players_used minutes_90s cards_yellow cards_red  \
0       América (MG)           32         9.0           26         1   
1     Atl Paranaense           26         9.0           25         1   
2   Atlético Mineiro           25         9.0           35         1   
3              Bahia           24         9.0           26         2   
4      Botafogo (RJ)           28         9.0           21         1   
5         Bragantino           25         9.0           28         2   
6        Corinthians           29         9.0           21         0   
7           Coritiba           28         9.0           35         1   
8           Cruzeiro           23         9.0           30         1   
9             Cuiabá           23         9.0           30         2   
10          Flamengo           24         9.0           18         0   
11        Fluminense           25         9.0           28         1   
12         Fortaleza           24         9.0           20         1   
13             Goiás           28         9.0           28         2   
14            Grêmio           28         9.0           30         1   
15     Internacional           26         9.0           23         0   
16         Palmeiras           26         9.0           26         0   
17            Santos           30         9.0           23         2   
18         São Paulo           24         9.0           23         1   
19     Vasco da Gama           26         9.0           25         0   

   cards_yellow_red fouls fouled offsides crosses interceptions tackles_won  \
0                 0   140    116       22     174            96          79   
1                 0   125    126       17     156            90          87   
2                 1   158    115       15     163            72         120   
3                 2   148    138        9     174           105          98   
4                 1   130    111       14     148           106          85   
5                 1   159    103       18     183            93          90   
6                 0   123    119       13     141            84          95   
7                 1   144    130       15     131            83         103   
8                 1   142    118       23     224           108          99   
9                 2   115    148       16     189            85          98   
10                0   132    122       18     154            77          95   
11                0   103    145       17     161            57          82   
12                1   113    115       17     194            82         116   
13                1   142    166       22     196            75          90   
14                1   113    129       16     122            95          95   
15                0   108    117       16     169            99          93   
16                0   150    137       18     217            81          82   
17                1   135    121       18     143            91         116   
18                1   128    114       15     164            76          97   
19                0   140    123       17     217            76          95   

   pens_won pens_conceded own_goals ball_recoveries aerials_won aerials_lost  \
0         1             3         1             513         164          145   
1         0             1         0             461         151          158   
2         2             1         0             481         110          124   
3         0             1         0             509         116          104   
4         3             0         0             445         116          108   
5         0             3         0             521         124          154   
6         2             2         0             437         104          114   
7         0             2         1             458         115          146   
8         1             1         0             503         123          137   
9         0             1         0        

In [50]:
pag_diversas = gs.worksheet('Diversos')

pag_diversas.clear()
set_with_dataframe(worksheet=pag_diversas, dataframe=df_stats_diversas, include_index=False,
include_column_header=True, resize=True)